### Json -> YOLO

In [ ]:
import os
import json
import glob
import shutil
from pathlib import Path

# YOLO 데이터셋 저장 경로
dataset_root = "data"
output_dir = "yolo_dataset"
os.makedirs(output_dir, exist_ok=True)

# YOLO 데이터셋 구조 생성
os.makedirs(f"{output_dir}/images/train", exist_ok=True)
os.makedirs(f"{output_dir}/labels/train", exist_ok=True)
os.makedirs(f"{output_dir}/images/val", exist_ok=True)
os.makedirs(f"{output_dir}/labels/val", exist_ok=True)

# 클래스 ID 매핑
class_to_id = {}
category_file = glob.glob(f"{dataset_root}/1.Training/labels/train/*.json")[0]  # 샘플 JSON
with open(category_file, "r", encoding="utf-8") as f:
    data = json.load(f)
    for category in data["categories"]:
        class_to_id[category["class_name"]] = category["class_id"]

print("클래스 매핑:", class_to_id)


# JSON → YOLO 변환 함수
def convert_to_yolo_format(annotation, img_width, img_height):
    if img_width == 0 or img_height == 0:
        raise ValueError(f"🚨 이미지 크기가 잘못되었습니다! (width={img_width}, height={img_height})")

    class_id = annotation["category_id"]
    x_min, y_min, box_w, box_h = annotation["bbox"]

    # YOLO 비율 변환
    x_center = (x_min + box_w / 2) / img_width
    y_center = (y_min + box_h / 2) / img_height
    width = box_w / img_width
    height = box_h / img_height

    return f"{class_id} {x_center:.6f} {y_center:.6f} {width:.6f} {height:.6f}\n"


# 데이터 변환 실행
for split, img_path, label_path in [
    ("train", "1.Training/images/train", "1.Training/labels/train"),
    ("val", "2.Validation/images/val", "2.Validation/labels/val")
]:
    image_dir = f"{dataset_root}/{img_path}"
    label_dir = f"{dataset_root}/{label_path}"

    for json_file in glob.glob(f"{label_dir}/*.json"):
        with open(json_file, "r", encoding="utf-8") as f:
            data = json.load(f)

        image_info = data["images"][0]
        img_width, img_height = image_info["width"], image_info["height"]

        print(f"📌 {json_file} - width: {img_width}, height: {img_height}")

        if img_width == 0 or img_height == 0:
            print(f"🚨 경고: {json_file} 에서 이미지 크기가 0입니다. 해당 파일을 건너뜁니다.")
            continue  # 스킵

        img_name = image_info["file_name"]
        img_src_path = f"{image_dir}/{img_name}"
        img_dst_path = f"{output_dir}/images/{split}/{img_name}"

        # 🔍 디버깅 로그
        print(f"🔍 원본 경로: {img_src_path}")
        print(f"🔍 복사 경로: {img_dst_path}")

        # 원본 이미지 존재 여부 확인
        if not os.path.exists(img_src_path):
            print(f"🚨 원본 이미지가 존재하지 않습니다: {img_src_path}")
            continue

        # 디렉토리 생성
        os.makedirs(f"{output_dir}/images/{split}", exist_ok=True)
        os.makedirs(f"{output_dir}/labels/{split}", exist_ok=True)

        # 이미지 복사
        try:
            shutil.copy(img_src_path, img_dst_path)
            print(f"✅ {img_name} 복사 완료!")
        except Exception as e:
            print(f"🚨 이미지 복사 오류: {e}")

        # YOLO 라벨 파일 생성
        label_path = f"{output_dir}/labels/{split}/{Path(img_name).stem}.txt"
        with open(label_path, "w") as f:
            for annotation in data["annotations"]:
                yolo_line = convert_to_yolo_format(annotation, img_width, img_height)
                f.write(yolo_line)

print("✅ 데이터 변환 완료! YOLO 형식으로 저장됨.")


클래스 매핑: {'매실': 85, '무화과': 86, '체리': 87, '복분자': 88, '복숭아': 89, '천도복숭아': 90, '블랙베리': 91, '블루베리': 92, '산딸기': 93, '자두': 94, '포도(송이)': 95, '감': 96, '대추': 97, '머루(송이)': 98, '모과': 99, '배': 100, '사과': 101, '석류': 102, '유자': 103, '귤': 104, '천혜향': 105, '한라봉': 106, '딸기': 107, '수박': 108, '참외': 109, '멜론': 110, '파인애플': 111, '바나나': 112, '용과': 113, '아보카도': 114, '자몽': 115, '두리안': 116, '망고스틴': 117, '망고': 118, '구아바': 119, '리치': 120, '파파야': 121, '람부탄': 122, '패션후르츠': 123, '레몬': 124, '키위': 125}
📌 data/1.Training/labels/train\1000421_591.json - width: 2800, height: 2100
📌 data/1.Training/labels/train\1000535_591.json - width: 2800, height: 2100
📌 data/1.Training/labels/train\1001083_591.json - width: 2800, height: 2100
📌 data/1.Training/labels/train\1001090_591.json - width: 2800, height: 2100
📌 data/1.Training/labels/train\1001096_591.json - width: 2800, height: 2100
📌 data/1.Training/labels/train\1001104_591.json - width: 2800, height: 2100
📌 data/1.Training/labels/train\1001111_591.json - width: 2800, heig

KeyboardInterrupt: 

### YOLO -> yaml

In [5]:
import os
import json
import glob
from pathlib import Path
dataset_root = "data"
output_dir = "yolo_dataset"
dataset_yaml = f"{output_dir}/dataset.yaml"
# 클래스 ID 매핑
class_to_id = {}
category_file = glob.glob(f"{dataset_root}/1.Training/labels/train/fruit01/*.json")[0]  # 샘플 JSON
with open(category_file, "r", encoding="utf-8") as f:
    data = json.load(f)
    for category in data["categories"]:
        class_to_id[category["class_name"]] = category["class_id"]

print("클래스 매핑:", class_to_id)

with open(dataset_yaml, "w") as f:
    f.write(f"train: {output_dir}/images/train\n")
    f.write(f"val: {output_dir}/images/val\n\n")
    f.write(f"nc: {len(class_to_id)}\n")
    f.write(f"names: {list(class_to_id.keys())}\n")

print(f"✅ {dataset_yaml} 생성 완료!")

클래스 매핑: {'매실': 85, '무화과': 86, '체리': 87, '복분자': 88, '복숭아': 89, '천도복숭아': 90, '블랙베리': 91, '블루베리': 92, '산딸기': 93, '자두': 94, '포도(송이)': 95, '감': 96, '대추': 97, '머루(송이)': 98, '모과': 99, '배': 100, '사과': 101, '석류': 102, '유자': 103, '귤': 104, '천혜향': 105, '한라봉': 106, '딸기': 107, '수박': 108, '참외': 109, '멜론': 110, '파인애플': 111, '바나나': 112, '용과': 113, '아보카도': 114, '자몽': 115, '두리안': 116, '망고스틴': 117, '망고': 118, '구아바': 119, '리치': 120, '파파야': 121, '람부탄': 122, '패션후르츠': 123, '레몬': 124, '키위': 125}
✅ yolo_dataset/dataset.yaml 생성 완료!
